# **Synthetic Dataset Generation for Soccer Training & Matches**

In [27]:
# ===================================================================
# Setup
# ===================================================================

import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from google.colab import drive
drive.mount('/content/drive')

# ----------------------------
# Settings (edit as needed)
# ----------------------------
OUT_PATH = "/content/drive/MyDrive/PORTFOLIO/Proyectos/App_Predicción_Cargas_Sesion/synthetic_full_dataset.csv"
np.random.seed(42)

teams = ["U23", "U21", "U19", "C Team", "B Team", "First Team"]
max_players_per_team = 20            # roster size per team (Player_01 .. Player_20)
weeks = 12                           # number of microcycles/weeks to simulate
start_date = datetime(2025, 1, 1)    # starting date for the first week

# label sequence applied per team (keeps relative order)
label_sequence = ["MD", "MD+1", "MD+2", "MD-4", "MD-3", "MD-2", "MD-1"]

# Task types (training)
task_types = ["Possession", "Conditioned Match", "Transition", "Passing Drill", "Warmup"]

min_tasks = 3
max_tasks = 6

# Match parameters
match_starters = 11
match_subs_min = 3
match_subs_max = 5

# Speed zone name mapping (we will output with the exact names you requested)
speed_zone_cols = [
    "Speed Zones (m) [0.0, 6.0]",
    "Speed Zones (m) [6.0, 12.0]",
    "Speed Zones (m) [12.0, 18.0]",
    "Speed Zones (m) [18.0, 21.0]",
    "Speed Zones (m) [21.0, 24.0]",
    "Speed Zones (m) [24.0, 50.0]"
]

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [28]:
# ----------------------------
# Helper functions
# ----------------------------
def sample_task_conditioners(task_type):
    """Return duration (min), base_distance (per-player baseline) and pitch size (length,width)."""
    if task_type == "Possession":
        duration = int(np.random.choice([8,10,12,15,18,20]))
        base_distance = np.random.normal(800,120) * (duration/20)
    elif task_type == "Conditioned Match":
        duration = int(np.random.choice([10,15,20,25,30]))
        base_distance = np.random.normal(1800,200) * (duration/20)
    elif task_type == "Transition":
        duration = int(np.random.choice([8,10,12,15]))
        base_distance = np.random.normal(1200,150) * (duration/20)
    elif task_type == "Passing Drill":
        duration = int(np.random.choice([5,6,8,10,12]))
        base_distance = np.random.normal(400,50) * (duration/20)
    else:  # Warmup
        duration = int(np.random.choice([5,6,8,10]))
        base_distance = np.random.normal(300,30) * (duration/20)

    length = int(np.random.randint(30, 90))   # meters
    width  = int(np.random.randint(20, 70))   # meters
    return {
        "duration_min": max(1, duration),
        "base_distance": max(10.0, float(base_distance)),
        "length_m": length,
        "width_m": width
    }

def adjust_speed_zone_allocation(zones, space_factor):
    """
    Adjust speed zone distribution according to space per player:
    - If space_factor > 1: shift mass to higher-speed zones (indices >=2)
    - If space_factor < 1: shift mass to low-speed zones (indices 0-1)
    We then normalize to keep sum == total distance.
    """
    zones = np.array(zones, dtype=float)
    total = zones.sum()
    if total <= 0:
        return zones
    # apply multipliers
    low_mult  = np.clip(1.0 / space_factor, 0.6, 1.6)
    high_mult = np.clip(space_factor, 0.6, 1.6)
    zones[:2] *= low_mult      # 0-6, 6-12
    zones[2:] *= high_mult     # 12-18 and above
    # renormalize to original total
    if zones.sum() <= 0:
        return zones
    zones = zones * (total / zones.sum())
    return zones

def gen_task_base_outputs(task_type, duration_min, players_team1, players_team2, jokers, length_m, width_m):
    """
    Generate task-level base outputs (per-player baseline) influenced by:
     - task_type
     - space per player = (length*width)/total_players
     - players_team1 / team2 / jokers
    Returns dictionary with keys matching your requested naming.
    """
    total_players_in_task = max(1, players_team1 + players_team2 + jokers)
    area = length_m * width_m
    space_per_player = area / total_players_in_task            # m^2 per player
    # normalize around 100 m2/player baseline (typical)
    space_factor = np.clip(space_per_player / 100.0, 0.4, 2.0)  # 0.4..2.0 range

    # base distance and lambdas derived from task type
    if task_type == "Possession":
        base_dist = np.random.normal(800,120) * (duration_min/20)
        acc_lambda, dec_lambda = 12, 12
        max_acc = np.random.uniform(3.5,5)
        max_dec = np.random.uniform(3.0,4.5)
        base_zone_weights = np.array([5,10,3,1,1,0.5])
    elif task_type == "Conditioned Match":
        base_dist = np.random.normal(1800,200) * (duration_min/20)
        acc_lambda, dec_lambda = 6, 6
        max_acc = np.random.uniform(3.0,4.0)
        max_dec = np.random.uniform(3.0,4.0)
        base_zone_weights = np.array([3,6,5,3,2,1])
    elif task_type == "Transition":
        base_dist = np.random.normal(1200,150) * (duration_min/20)
        acc_lambda, dec_lambda = 10, 10
        max_acc = np.random.uniform(3.2,4.8)
        max_dec = np.random.uniform(3.0,4.2)
        base_zone_weights = np.array([4,7,4,2,2,1])
    elif task_type == "Passing Drill":
        base_dist = np.random.normal(400,50) * (duration_min/20)
        acc_lambda, dec_lambda = 4, 4
        max_acc = np.random.uniform(2.2,3.5)
        max_dec = np.random.uniform(1.8,3.0)
        base_zone_weights = np.array([8,10,2,0.5,0.2,0.1])
    else:  # Warmup
        base_dist = np.random.normal(300,30) * (duration_min/20)
        acc_lambda, dec_lambda = 3, 3
        max_acc = np.random.uniform(1.8,3.0)
        max_dec = np.random.uniform(1.2,2.5)
        base_zone_weights = np.array([10,8,2,0.5,0.2,0.1])

    base_dist = float(max(5.0, base_dist))  # ensure positive

    # Influence of space: more space -> more distance and HSR; less space -> more acc/dec events
    # distance multiplier
    dist_multiplier = 1.0 + 0.25 * (space_factor - 1.0)   # up to ~+25% if lots of space, down if little
    base_dist *= dist_multiplier

    # acc/dec multiplier (inverse of space)
    acc_dec_multiplier = np.clip(1.0 / space_factor, 0.6, 1.8)

    # sample counts (team-level baseline per player)
    acc_count = int(np.random.poisson(max(0.1, acc_lambda * acc_dec_multiplier)))
    dec_count = int(np.random.poisson(max(0.1, dec_lambda * acc_dec_multiplier)))

    acc_m = acc_count * np.random.uniform(0.35, 1.2)
    dec_m = dec_count * np.random.uniform(0.35, 1.2)

    # speed zone base split (dirichlet)
    alphas = base_zone_weights + 0.5 * np.random.rand(len(base_zone_weights))
    props = np.random.dirichlet(alphas)
    raw_zones = props * base_dist
    # adjust high/low speed according to space factor
    zones = adjust_speed_zone_allocation(raw_zones, space_factor)

    # HSR as sum of higher zones (index 2..5)
    hsr_m = float(zones[2:].sum())

    out = {
        "Distance - Distance (m)": float(base_dist),
        "Distance - Abs HSR (m)": float(max(0.0, hsr_m)),
        "Distance - HSR Rel (m/min)": float(hsr_m / max(1.0, duration_min)),
        "Distance - Abs HSR (% of distance)": float(100.0 * (hsr_m / max(1e-6, base_dist))),
        "Distance - HIA": int(acc_count),
        "Distance - HIBD (m)": float(dec_m),
        "Accelerations - High Intensity Acc Abs (count)": int(acc_count),
        "Accelerations - High Intensity Acc Abs (m)": float(acc_m),
        "Accelerations - High Intensity Dec Abs (count)": int(dec_count),
        "Accelerations - High Intensity Dec Abs (m)": float(dec_m),
        "Accelerations - Max Acceleration (m/s²)": float(round(max_acc,3)),
        "Accelerations - Max Deceleration (m/s²)": float(round(max_dec,3)),
        # speed zones (keep the exact column names)
        speed_zone_cols[0]: float(zones[0]),
        speed_zone_cols[1]: float(zones[1]),
        speed_zone_cols[2]: float(zones[2]),
        speed_zone_cols[3]: float(zones[3]),
        speed_zone_cols[4]: float(zones[4]),
        speed_zone_cols[5]: float(zones[5]),
        # meta
        "Space_per_player_m2": float(space_per_player),
        "space_factor": float(space_factor),
        "players_total_in_task": int(total_players_in_task)
    }
    return out


In [29]:
# ----------------------------
# Main generation loop
# ----------------------------
rows = []
current_global_date = start_date

for team in teams:
    # roster for the team
    players = [f"Player_{i+1:02d}" for i in range(max_players_per_team)]

    # build team-specific dates while preserving label order; allow random missing days
    team_dates = []
    for w in range(weeks):
        base = current_global_date + timedelta(days=7*w)
        for offset in range(len(label_sequence)):
            team_dates.append(base + timedelta(days=offset))

    # randomly drop a few team days (simulate missing sessions)
    drop_mask = np.random.rand(len(team_dates)) < 0.05
    team_dates = [d for i,d in enumerate(team_dates) if not drop_mask[i]]

    label_idx = 0
    for day in sorted(team_dates):
        label = label_sequence[label_idx % len(label_sequence)]
        label_idx += 1

        if label == "MD":
            # Match day: starters + subs (match for this team)
            starters = list(np.random.choice(players, size=match_starters, replace=False))
            n_subs = int(np.random.randint(match_subs_min, match_subs_max+1))
            subs = list(np.random.choice([p for p in players if p not in starters], size=n_subs, replace=False))
            # match-level pitch approx
            length_m = int(np.random.randint(90, 105))
            width_m  = int(np.random.randint(60, 75))
            players_team1 = match_starters  # team players on pitch
            players_team2 = match_starters  # opponent (not tracked as roster)
            jokers = 0
            goalkeepers = 2  # both teams each have a GK
            total_players = players_team1 + players_team2  # on-pitch counting both teams (approx)
            # For each participating player (starters + subs), create a row (some subs may not play)
            task_id = f"{team}_{day.strftime('%Y%m%d')}_MATCH"
            for p in starters + subs:
                # determine minutes played and participation
                if p in starters:
                    minutes_played = int(np.random.randint(65, 91))
                    played = True
                    indiv_multiplier = np.random.uniform(0.7, 1.0)
                else:
                    # subs: some may not play
                    played = np.random.rand() < 0.85
                    minutes_played = int(np.random.randint(5, 45)) if played else 0
                    indiv_multiplier = np.random.uniform(0.15, 0.6) if played else 0.0

                if (not played) and (np.random.rand() < 0.5):
                    # skip row half the time (no data)
                    continue

                # base outputs per-player for match scaled by minutes
                base_dist_for_player = np.random.normal(10000, 800) * (minutes_played / 90.0)
                match_base = gen_task_base_outputs("Conditioned Match", max(1, minutes_played),
                                                   players_team1, players_team2, jokers,
                                                   length_m, width_m)
                # scale per player using indiv_multiplier
                row = {
                    "Date": day.date().isoformat(),
                    "DayLabel": label,
                    "Team": team,
                    "Player": p,
                    "TaskID": task_id,
                    "TaskType": "Match",
                    "Length (m)": length_m,
                    "Width (m)": width_m,
                    "Duration (min)": minutes_played,
                    "Players_Team1": players_team1,
                    "Players_Team2": players_team2,
                    "Jokers": jokers,
                    "Goalkeepers": goalkeepers,
                    "Total_Players": int(players_team1 + players_team2 + jokers),
                    "Density (m2/player)": (length_m * width_m) / max(1, (players_team1 + players_team2 + jokers))
                }
                # conditional outputs: take base and scale
                for k, v in match_base.items():
                    if k in ["Space_per_player_m2", "space_factor", "players_total_in_task"]:
                        # keep numeric metadata if helpful
                        row[k] = v
                        continue
                    if isinstance(v, (int, float, np.floating, np.integer)):
                        # scale numeric outputs by individual multiplier with some noise
                        row[k] = float(max(0.0, v * indiv_multiplier * np.random.uniform(0.85, 1.15)))
                    else:
                        row[k] = v
                rows.append(row)

        else:
            # Training day: multiple tasks with two internal teams + jokers + optionally GK
            n_tasks = int(np.random.randint(min_tasks, max_tasks+1))
            for t_idx in range(n_tasks):
                task_type = np.random.choice(task_types, p=[0.25, 0.15, 0.2, 0.25, 0.15])
                cond = sample_task_conditioners(task_type)
                length_m = cond["length_m"]
                width_m  = cond["width_m"]
                duration_min = cond["duration_min"]

                # decide how many players per team for this specific task (must fit roster)
                # reasonable ranges for small-sided to full-sided drills
                players_team1 = int(np.random.randint(4, min(12, max_players_per_team-2)))
                players_team2 = int(np.random.randint(4, min(12, max_players_per_team - players_team1)))
                jokers = int(np.random.randint(0, 3))  # 0-2 jokers
                # decide if GKs included (probabilistic)
                include_gks = np.random.rand() < 0.6  # 60% tasks include GKs practice
                goalkeepers = 2 if include_gks else 0
                total_players = players_team1 + players_team2 + jokers + goalkeepers

                # generate task-level base outputs (per-player baseline)
                base_outputs = gen_task_base_outputs(task_type, duration_min,
                                                     players_team1, players_team2, jokers,
                                                     length_m, width_m)

                task_id = f"{team}_{day.strftime('%Y%m%d')}_T{t_idx+1}"

                # select which players will take part in this task (sample without replacement)
                # ensure enough available players in roster
                participants = list(np.random.choice(players, size=min(max_players_per_team, total_players + int(0.4*max_players_per_team)), replace=False))
                # But we will only mark team1/team2/jokers slots
                # Pick team1_players from participants
                t1_players = list(np.random.choice(participants, size=min(players_team1, len(participants)), replace=False))
                remaining = [p for p in participants if p not in t1_players]
                t2_size = min(players_team2, len(remaining))
                t2_players = list(np.random.choice(remaining, size=t2_size, replace=False))
                remaining = [p for p in remaining if p not in t2_players]
                # jokers come from remaining
                jokers_selected = list(np.random.choice(remaining, size=min(jokers, len(remaining)), replace=False)) if len(remaining)>0 else []
                # if we don't have enough distinct players, some players may appear in multiple roles (fine for simulation)

                # Build per-player rows
                # For each participant (union of groups)
                participants_union = list(dict.fromkeys(t1_players + t2_players + jokers_selected))  # preserve order, unique
                for p in participants_union:
                    # attendance noise: some players might not fully participate
                    attend_prob = 0.95
                    attends = np.random.rand() < attend_prob
                    if not attends and (np.random.rand() < 0.6):
                        # skip row (didn't attend or present)
                        continue
                    # individual multiplier around 1.0
                    indiv_mult = float(np.clip(np.random.normal(1.0, 0.12), 0.5, 1.6))
                    # if player is a joker, slightly different multiplier
                    if p in jokers_selected:
                        indiv_mult *= np.random.uniform(0.85, 1.05)
                    # determine minutes played in task (for variability)
                    minutes_played = duration_min  # assume full duration normally
                    if np.random.rand() < 0.08:
                        minutes_played = int(np.random.randint(1, duration_min+1))

                    row = {
                        "Date": day.date().isoformat(),
                        "DayLabel": label,
                        "Team": team,
                        "Player": p,
                        "TaskID": task_id,
                        "TaskType": task_type,
                        "Length (m)": length_m,
                        "Width (m)": width_m,
                        "Duration (min)": minutes_played,
                        "Players_Team1": players_team1,
                        "Players_Team2": players_team2,
                        "Jokers": jokers,
                        "Goalkeepers": goalkeepers,
                        "Total_Players": total_players,
                        "Density (m2/player)": (length_m * width_m) / max(1, total_players)
                    }
                    # conditional outputs: scale base outputs by individual multiplier and small noise
                    for k, v in base_outputs.items():
                        if k in ["Space_per_player_m2", "space_factor", "players_total_in_task"]:
                            # preserve base meta if helpful
                            row[k] = v
                            continue
                        # numeric output scaling
                        if isinstance(v, (int, float, np.floating, np.integer)):
                            noise = np.random.uniform(0.9, 1.1)
                            val = float(max(0.0, v * indiv_mult * noise))
                            # counts should be integers when appropriate
                            if ("count" in k) or (k in ["Distance - HIA", "Accelerations - High Intensity Acc Abs (count)", "Accelerations - High Intensity Dec Abs (count)"]):
                                row[k] = int(round(val))
                            else:
                                row[k] = float(val)
                        else:
                            row[k] = v
                    rows.append(row)


In [30]:
# ----------------------------
# Build DataFrame & Save
# ----------------------------
df = pd.DataFrame(rows)

# standardize column order a bit
# meta columns first
meta_cols = ["Date", "DayLabel", "Team", "Player", "TaskID", "TaskType",
             "Length (m)", "Width (m)", "Duration (min)",
             "Players_Team1", "Players_Team2", "Jokers", "Goalkeepers", "Total_Players", "Density (m2/player)"]
# then conditional columns (ensure they exist)
cond_cols = [
    "Distance - Distance (m)",
    "Distance - Abs HSR (m)",
    "Distance - HSR Rel (m/min)",
    "Distance - Abs HSR (% of distance)",
    "Distance - HIA",
    "Distance - HIBD (m)",
    "Accelerations - High Intensity Acc Abs (count)",
    "Accelerations - High Intensity Acc Abs (m)",
    "Accelerations - High Intensity Dec Abs (count)",
    "Accelerations - High Intensity Dec Abs (m)",
    "Accelerations - Max Acceleration (m/s²)",
    "Accelerations - Max Deceleration (m/s²)"
] + speed_zone_cols + ["Space_per_player_m2", "space_factor", "players_total_in_task"]

# keep only columns present
all_cols = [c for c in meta_cols + cond_cols if c in df.columns]
df = df[all_cols]

# add iso-week and weekday for convenience
df['Date'] = pd.to_datetime(df['Date'])
df['iso_week'] = df['Date'].dt.isocalendar().week
df['weekday'] = df['Date'].dt.day_name()

print("Generated rows:", len(df))
print("Columns:", df.columns.tolist())

# Save CSV
df.to_csv(OUT_PATH, index=False)
print("Saved synthetic dataset to:", OUT_PATH)

Generated rows: 28674
Columns: ['Date', 'DayLabel', 'Team', 'Player', 'TaskID', 'TaskType', 'Length (m)', 'Width (m)', 'Duration (min)', 'Players_Team1', 'Players_Team2', 'Jokers', 'Goalkeepers', 'Total_Players', 'Density (m2/player)', 'Distance - Distance (m)', 'Distance - Abs HSR (m)', 'Distance - HSR Rel (m/min)', 'Distance - Abs HSR (% of distance)', 'Distance - HIA', 'Distance - HIBD (m)', 'Accelerations - High Intensity Acc Abs (count)', 'Accelerations - High Intensity Acc Abs (m)', 'Accelerations - High Intensity Dec Abs (count)', 'Accelerations - High Intensity Dec Abs (m)', 'Accelerations - Max Acceleration (m/s²)', 'Accelerations - Max Deceleration (m/s²)', 'Speed Zones (m) [0.0, 6.0]', 'Speed Zones (m) [6.0, 12.0]', 'Speed Zones (m) [12.0, 18.0]', 'Speed Zones (m) [18.0, 21.0]', 'Speed Zones (m) [21.0, 24.0]', 'Speed Zones (m) [24.0, 50.0]', 'Space_per_player_m2', 'space_factor', 'players_total_in_task', 'iso_week', 'weekday']
Saved synthetic dataset to: /content/drive/MyDri

In [31]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [32]:
df.head(3000)

Date DayLabel Team     Player              TaskID  \
0    2025-01-01       MD  U23  Player_07  U23_20250101_MATCH   
1    2025-01-01       MD  U23  Player_04  U23_20250101_MATCH   
2    2025-01-01       MD  U23  Player_17  U23_20250101_MATCH   
3    2025-01-01       MD  U23  Player_09  U23_20250101_MATCH   
4    2025-01-01       MD  U23  Player_10  U23_20250101_MATCH   
5    2025-01-01       MD  U23  Player_16  U23_20250101_MATCH   
6    2025-01-01       MD  U23  Player_02  U23_20250101_MATCH   
7    2025-01-01       MD  U23  Player_15  U23_20250101_MATCH   
8    2025-01-01       MD  U23  Player_13  U23_20250101_MATCH   
9    2025-01-01       MD  U23  Player_18  U23_20250101_MATCH   
10   2025-01-01       MD  U23  Player_20  U23_20250101_MATCH   
11   2025-01-01       MD  U23  Player_19  U23_20250101_MATCH   
12   2025-01-01       MD  U23  Player_08  U23_20250101_MATCH   
13   2025-01-01       MD  U23  Player_03  U23_20250101_MATCH   
14   2025-01-01       MD  U23  Player_11  U23_20250101_MATCH   
15   2025-01-02     MD+1  U23  Player_20     U23_20250102_T1   
16   2025-01-02     MD+1  U23  Player_04     U23_20250102_T1   
17   2025-01-02     MD+1  U23  Player_08     U23_20250102_T1   
18   2025-01-02     MD+1  U23  Player_10     U23_20250102_T1   
19   2025-01-02     MD+1  U23  Player_16     U23_20250102_T1   
20   2025-01-02     MD+1  U23  Player_12     U23_20250102_T1   
21   2025-01-02     MD+1  U23  Player_09     U23_20250102_T1   
22   2025-01-02     MD+1  U23  Player_18     U23_20250102_T1   
23   2025-01-02     MD+1  U23  Player_17     U23_20250102_T1   
24   2025-01-02     MD+1  U23  Player_02     U23_20250102_T1   
25   2025-01-02     MD+1  U23  Player_19     U23_20250102_T1   
26   2025-01-02     MD+1  U23  Player_15     U23_20250102_T1   
27   2025-01-02     MD+1  U23  Player_06     U23_20250102_T1   
28   2025-01-02     MD+1  U23  Player_13     U23_20250102_T1   
29   2025-01-02     MD+1  U23  Player_03     U23_20250102_T1   
30   2025-01-02     MD+1  U23  Player_14     U23_20250102_T2   
31   2025-01-02     MD+1  U23  Player_16     U23_20250102_T2   
32   2025-01-02     MD+1  U23  Player_06     U23_20250102_T2   
33   2025-01-02     MD+1  U23  Player_02     U23_20250102_T2   
34   2025-01-02     MD+1  U23  Player_03     U23_20250102_T2   
35   2025-01-02     MD+1  U23  Player_11     U23_20250102_T2   
36   2025-01-02     MD+1  U23  Player_17     U23_20250102_T2   
37   2025-01-02     MD+1  U23  Player_05     U23_20250102_T2   
38   2025-01-02     MD+1  U23  Player_15     U23_20250102_T2   
39   2025-01-02     MD+1  U23  Player_09     U23_20250102_T2   
40   2025-01-02     MD+1  U23  Player_19     U23_20250102_T2   
41   2025-01-02     MD+1  U23  Player_13     U23_20250102_T2   
42   2025-01-02     MD+1  U23  Player_08     U23_20250102_T2   
43   2025-01-02     MD+1  U23  Player_10     U23_20250102_T2   
44   2025-01-02     MD+1  U23  Player_20     U23_20250102_T2   
45   2025-01-02     MD+1  U23  Player_01     U23_20250102_T2   
46   2025-01-02     MD+1  U23  Player_18     U23_20250102_T2   
47   2025-01-02     MD+1  U23  Player_12     U23_20250102_T2   
48   2025-01-02     MD+1  U23  Player_15     U23_20250102_T3   
49   2025-01-02     MD+1  U23  Player_08     U23_20250102_T3   
50   2025-01-02     MD+1  U23  Player_14     U23_20250102_T3   
51   2025-01-02     MD+1  U23  Player_20     U23_20250102_T3   
52   2025-01-02     MD+1  U23  Player_16     U23_20250102_T3   
53   2025-01-02     MD+1  U23  Player_09     U23_20250102_T3   
54   2025-01-02     MD+1  U23  Player_07     U23_20250102_T3   
55   2025-01-02     MD+1  U23  Player_12     U23_20250102_T3   
56   2025-01-02     MD+1  U23  Player_03     U23_20250102_T3   
57   2025-01-02     MD+1  U23  Player_18     U23_20250102_T3   
58   2025-01-02     MD+1  U23  Player_05     U23_20250102_T3   
59   2025-01-02     MD+1  U23  Player_04     U23_20250102_T3   
60   2025-01-03     MD+2  U23  Player_16     U23_20250103_T1   
61   2025-01-03     MD+2  U23  Player_07   